In [1]:
# Import General libraries
import pandas as pd
import numpy as np
import math


# For Visualizations
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

# For the Tilelayer of NYC Neighborhoods
import json

# To see full column values
pd.set_option('max_colwidth', 800)
pd.options.display.float_format = '{:,.2f}'.format

In [2]:
# Create path
file = "Resources/geopyoutput.csv"

# Read in file
df = pd.read_csv(file)

# Drop 2nd index
df = df.loc[:, ~df.columns.str.contains('^Unnamed')]

# Display first 5 Records
df.head()

Street       Unit   Borough                Neighborhood  \
0       9602 4th Avenue         6D  Brooklyn                   Bay Ridge   
1      94 Degraw Street        NaN  Brooklyn  Columbia Street Waterfront   
2  933 Lafayette Street  1st floor  Brooklyn          Bedford-Stuyvesant   
3     918 Manhattan Ave         #2  Brooklyn                  Greenpoint   
4    906 Prospect Place         2A  Brooklyn               Crown Heights   

       City     State        Year        Price  Status  Postalcode  \
0  New York  New York  2019-01-01          NaN  Rental       11209   
1  Brooklyn  New York  2020-01-01 2,350,000.00    Sale       11231   
2  Brooklyn  New York  2020-01-01 1,095,000.00    Sale       11221   
3  Brooklyn  New York  2021-01-01     5,000.00  Rental       11222   
4  Brooklyn  New York  2021-01-01   735,000.00    Sale       11213   

                                          Location  \
0       9602 4th Avenue, New York, New York, 11209   
1      94 Degraw Street, Brooklyn, New York, 11231   
2  933 Lafayette Street, Brooklyn, New York, 11221   
3     918 Manhattan Ave, Brooklyn, New York, 11222   
4    906 Prospect Place, Brooklyn, New York, 11213   

                                                                                                          Address  \
0                         9602, 4th Avenue, Fort Hamilton, Brooklyn, Kings County, New York, 11209, United States   
1  94, Degraw Street, Columbia Street Waterfront District, Brooklyn, Kings County, New York, 11231, United States   
2                                                                                                             NaN   
3          Green Farms Supermarket, 918, Manhattan Avenue, Brooklyn, Kings County, New York, 11222, United States   
4                    906, Prospect Place, Eastern Parkway, Brooklyn, Kings County, New York, 11213, United States   

                                           point  Latitude  Longitude  
0            (40.6151866, -74.032020545154, 0.0)     40.62     -74.03  
1  (40.685799349999996, -74.00335189192313, 0.0)     40.69     -74.00  
2                                            NaN     40.69     -73.93  
3                 (40.7307511, -73.9540256, 0.0)     40.73     -73.95  
4         (40.67376755, -73.94657791384977, 0.0)     40.67     -73.95

In [3]:
# Read in tilelayer geojson file

path = "Resources/nyc.geojson"

with open(path) as json_data:
    newyork_data = json.load(json_data)
    
newyork_data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'neighborhood': 'Allerton',
    'boroughCode': '2',
    'borough': 'Bronx',
    '@id': 'http://nyc.pediacities.com/Resource/Neighborhood/Allerton'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-73.84859700000018, 40.871670000000115],
      [-73.84582253683678, 40.870239076236174],
      [-73.85455918463374, 40.85995383576425],
      [-73.85466543306826, 40.859585694988056],
      [-73.85638870335896, 40.85759363530448],
      [-73.86888180915341, 40.857223150158326],
      [-73.86831755272824, 40.85786206225831],
      [-73.86955371467232, 40.85778409560018],
      [-73.87102485762065, 40.857309948816905],
      [-73.87048054998716, 40.865413584098484],
      [-73.87055489856489, 40.86970279858986],
      [-73.86721594442561, 40.86968966363671],
      [-73.85745, 40.86953300000018],
      [-73.85555000000011, 40.871813000000145],
      [-73.85359796757658, 40.8732883686742],
      [-73.848597

In [4]:
# Create a list of all lat/long coordinate pairs
locations = df[['Latitude', 'Longitude']]
locationlist = locations.values.tolist()
locationlist

[[40.6151866, -74.032020545154],
 [40.68579935, -74.00335189192313],
 [40.692015, -73.934678],
 [40.7307511, -73.9540256],
 [40.67376755, -73.94657791384977],
 [40.69886695, -73.93986610491517],
 [40.68560405, -73.92165635454509],
 [40.69052825, -73.93423862971204],
 [40.6786036, -73.96327695],
 [40.68824595, -73.92800579875049],
 [40.71529507692308, -74.00703146153846],
 [40.7112356, -73.9481786],
 [40.7112356, -73.9481786],
 [40.7112356, -73.9481786],
 [40.6941834, -73.99585531608435],
 [40.7266738, -73.94668815],
 [40.7266738, -73.94668815],
 [40.7247992, -73.94660784727965],
 [40.65299665, -73.91209596183775],
 [40.678081500000005, -73.98419386229119],
 [40.635121, -73.9615148],
 [40.6814318, -73.91167355],
 [40.7062521, -73.89861955],
 [40.68833835, -73.93710600950291],
 [40.72156795, -73.94240743840871],
 [40.68717169999999, -73.94380349754783],
 [40.68717169999999, -73.94380349754783],
 [40.68717169999999, -73.94380349754783],
 [40.68717169999999, -73.94380349754783],
 [40.68717

#### Map 1.0

In [5]:
# Create a map
m_1 = folium.Map(location=[40.6872, -73.9418], tiles='openstreetmap', zoom_start=12)

# Display the map
m_1

# Add points to the map
for idx, row in df.iterrows():
    folium.CircleMarker([row['Latitude'], row['Longitude']], # To create the circle markers loop through each row of Lat/Long data
                        radius = 5, # Change size of circle marker
                        popup= row[['Neighborhood', 'Price', 'Borough']]).add_to(m_1) # Dictate tool tip display data


# Display the map
m_1

# save method of Map object will create a map
#my_map1.save("my_map1.html")

In [6]:
df['Price'] = df.Price.fillna(0.0).astype(int)

#### Map 2.0 - Updating the icon using FontAwesome
* Follow link for access to icon documentation
https://fontawesome.com/v5.15/icons?d=gallery

In [7]:
# Create a map

m_2 = folium.Map(location=[40.6872, -73.9418], tiles='cartodbpositron', zoom_start=12)

# Display the map
m_2

# Add points to the map
for idx, row in df.iterrows():
    folium.Marker([row['Latitude'], row['Longitude']], # To create the circle markers loop through each row of Lat/Long data
                  popup=row[['Address','Neighborhood', 'Price', 'Borough']], # Dictate tool tip display data
                  icon=folium.Icon(color="black",icon="home", prefix='fa')).add_to(m_2) # Change icon from circle marker home icon

# Display the map
m_2

# save method of Map object will create a map
#my_map1.save("my_map1.html")

#### Map 3.0 - Tooltip Formatting

In [8]:
# Create a map
                
m_3 = folium.Map(location=[40.6872, -73.9418], tiles='cartodbpositron', zoom_start=12)


# Display the map
m_3

# Add points to the map
for idx, row in df.iterrows():
    address = getattr(row, "Street")
    unit = getattr(row, "Unit")
    neighborhood  = getattr(row, "Neighborhood")
    price  = getattr(row, "Price")
    borough  = getattr(row, "Borough")
    status  = getattr(row, "Status")
    folium.Marker([row['Latitude'], row['Longitude']],
                  popup=folium.Popup(f"""Address: {address} {unit} <br> Neighborhood: {neighborhood} <br> Price: {price} <br> Borough: {borough} <br> Transaction Type: {status}""", max_width=len(f"address= {address}")*20), icon=folium.Icon(color="black",icon="home", prefix='fa')).add_to(m_3)

# Display the map
m_3

#### Map 4.0 - Adding a Tile Layer

In [9]:
# Create a map
                
m_4 = folium.Map(location=[40.6872, -73.9418], tiles='cartodbpositron', zoom_start=12)


# Display the map
m_4

# Add points to the map
for idx, row in df.iterrows():
    address = getattr(row, "Street")
    unit = getattr(row, "Unit")
    neighborhood  = getattr(row, "Neighborhood")
    price  = getattr(row, "Price")
    borough  = getattr(row, "Borough")
    status  = getattr(row, "Status")
    folium.Marker([row['Latitude'], row['Longitude']],
                  radius = 5, 
                  popup=folium.Popup(f"""Address: {address} {unit} <br> Neighborhood: {neighborhood} <br> Price: {price} <br> Borough: {borough} <br> Transaction Type: {status}""", max_width=len(f"address= {address}")*20), icon=folium.Icon(color="black",icon="home", prefix='fa')).add_to(m_4)

layer = folium.GeoJson(
    data=(open(path, "r").read()),
    name='geojson',



).add_to(m_4) # 1. keep a reference to GeoJSON layer


m_4.fit_bounds(layer.get_bounds())  # 2. fit the map to GeoJSON layer 


# Display the map
m_4

